# Classification d'images sur CIFAR-10 avec un reseau de neurnoes convolutif en PyTorch

Import des bibliotheques

In [8]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F

import torchvision
import torchvision.transforms as transforms

import os

Definition du reseau convolutif

In [9]:
class LeNet(nn.Module):
    def __init__(self):
        super(LeNet, self).__init__()
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=6, kernel_size=5)
        self.conv2 = nn.Conv2d(6, 16, 5)
        self.fc1   = nn.Linear(in_features=16*5*5, out_features=120)
        self.fc2   = nn.Linear(120, 84)
        self.fc3   = nn.Linear(84, 10)

    def forward(self, x):
        out = F.relu(self.conv1(x))
        out = F.max_pool2d(out, 2)
        out = F.relu(self.conv2(out))
        out = F.max_pool2d(out, 2)
        out = out.view(out.size(0), -1)
        out = F.relu(self.fc1(out))
        out = F.relu(self.fc2(out))
        out = self.fc3(out)
        return out

Definition des donnees

In [10]:
# Data
print('==> Preparing data..')
transform_train = transforms.Compose([
    transforms.RandomCrop(32, padding=4),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
    transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
])

transform_test = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
])

trainset = torchvision.datasets.CIFAR10(
    root='./data', train=True, download=True, transform=transform_train)
trainloader = torch.utils.data.DataLoader(
    trainset, batch_size=128, shuffle=True, num_workers=2)

testset = torchvision.datasets.CIFAR10(
    root='./data', train=False, download=True, transform=transform_test)
testloader = torch.utils.data.DataLoader(
    testset, batch_size=100, shuffle=False, num_workers=2)

classes = ('plane', 'car', 'bird', 'cat', 'deer',
           'dog', 'frog', 'horse', 'ship', 'truck')


==> Preparing data..
Files already downloaded and verified
Files already downloaded and verified


Fonctions pour l'entrainement

In [11]:
def train(epoch):
    print('\nEpoch: %d' % epoch)
    net.train()
    train_loss = 0
    correct = 0
    total = 0
    for batch_idx, (inputs, targets) in enumerate(trainloader):
        inputs, targets = inputs.to(device), targets.to(device)
        optimizer.zero_grad()
        outputs = net(inputs)
        loss = criterion(outputs, targets)
        loss.backward()
        optimizer.step()

        train_loss += loss.item()
        _, predicted = outputs.max(1)
        total += targets.size(0)
        correct += predicted.eq(targets).sum().item()


    print(f'train loss: {train_loss/(batch_idx+1):.3f} | Acc: {100.*correct/total:.3f}%')
    return train_loss


def test(epoch):
    global best_acc
    net.eval()
    test_loss = 0
    correct = 0
    total = 0
    with torch.no_grad():
        for batch_idx, (inputs, targets) in enumerate(testloader):
            inputs, targets = inputs.to(device), targets.to(device)
            outputs = net(inputs)
            loss = criterion(outputs, targets)

            test_loss += loss.item()
            _, predicted = outputs.max(1)
            total += targets.size(0)
            correct += predicted.eq(targets).sum().item()
        print(f'Test loss: {test_loss/(batch_idx+1):.3f} | Acc: {100.*correct/total:.3f}%')

    # Save checkpoint.
    acc = 100.*correct/total
    if acc > best_acc:
        print('Saving..')
        state = {
            'net': net.state_dict(),
            'acc': acc,
            'epoch': epoch,
        }
        if not os.path.isdir('checkpoint'):
            os.mkdir('checkpoint')
        torch.save(state, './ckpt.pth')
        best_acc = acc
    return test_loss

In [12]:
lr = 0.1 # learning rate: pas dans la descente de gradient
resume = False # resume from checkpoint
device = 'cuda' if torch.cuda.is_available() else 'cpu'
best_acc = 0  # best test accuracy
start_epoch = 0  # start from epoch 0 or last checkpoint epoch


net = LeNet().to(device)

if resume:
    # Load checkpoint.
    print('==> Resuming from checkpoint..')
    checkpoint = torch.load('./ckpt.pth')
    net.load_state_dict(checkpoint['net'])
    best_acc = checkpoint['acc']
    start_epoch = checkpoint['epoch']

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=lr,
                      momentum=0.9, weight_decay=5e-4)
n_epochs = 50
scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=[35,45], gamma=0.1)


# Training


tr_losses, te_losses = [], []
for epoch in range(start_epoch, start_epoch+n_epochs):
    tr_losses.append(train(epoch))
    te_losses.append(test(epoch))
    scheduler.step()


Epoch: 0
train loss: 1.983 | Acc: 25.238%
Test loss: 1.890 | Acc: 29.210%
Saving..

Epoch: 1
train loss: 1.837 | Acc: 30.916%
Test loss: 1.793 | Acc: 30.900%
Saving..

Epoch: 2
train loss: 1.777 | Acc: 34.048%
Test loss: 1.720 | Acc: 35.480%
Saving..

Epoch: 3
train loss: 1.732 | Acc: 35.862%
Test loss: 1.638 | Acc: 38.820%
Saving..

Epoch: 4
train loss: 1.718 | Acc: 37.172%
Test loss: 1.623 | Acc: 41.070%
Saving..

Epoch: 5
train loss: 1.689 | Acc: 38.322%
Test loss: 1.642 | Acc: 40.770%

Epoch: 6
train loss: 1.670 | Acc: 39.272%
Test loss: 1.523 | Acc: 44.960%
Saving..

Epoch: 7
train loss: 1.684 | Acc: 38.556%
Test loss: 1.712 | Acc: 38.500%

Epoch: 8
train loss: 1.674 | Acc: 39.236%
Test loss: 1.651 | Acc: 41.690%

Epoch: 9
train loss: 1.666 | Acc: 39.646%
Test loss: 1.612 | Acc: 40.360%

Epoch: 10
train loss: 1.638 | Acc: 40.542%
Test loss: 1.557 | Acc: 45.190%
Saving..

Epoch: 11
train loss: 1.636 | Acc: 41.020%
Test loss: 1.603 | Acc: 41.550%

Epoch: 12
train loss: 1.621 | Acc: